In [15]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [16]:
# Path hack.
import sys
import os

sys.path.append(os.path.abspath(".."))

In [17]:
import csv
import ast
from datetime import date, datetime, time, timedelta
from datetime import datetime
import pickle as pkl
import time
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import StandardScaler

import numpy as np
import pandas as pd
import sklearn
from joblib import dump, load

import matplotlib.pyplot as plt

import torch
from torch.utils.data import Dataset, DataLoader
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms, utils

from models.simple_nn import *
from utils.simple_nn_utils import *
from utils.general_utils import *
from utils.data_loader import *

# Read in Dataset

In [18]:
from sklearn.ensemble import RandomForestClassifier
from xgboost import XGBClassifier
from sklearn.model_selection import cross_val_score

# from sklearn.metrics import confusion_matrix, recall_score, precision_score
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import StratifiedKFold


import optuna


import matplotlib.pyplot as plt
from sklearn.datasets import make_classification
from sklearn.metrics import ConfusionMatrixDisplay

In [19]:
data = pd.read_csv(
    f"/gpfs/milgram/project/rtaylor/shared/ABDPain_EarlyDiags/unq_pt_enc_single_label_clean_label_nomismatches.csv",
    #                   nrows=10000
)

In [20]:
# data['PAT_ENC_CSN_ID'].value_counts()
# data.iloc[:10,:].sum(axis=0)
data = data.rename(columns={"WikEM_overalltopic": "label"})

# data = data.fillna(0)
data.columns = data.columns.str.replace("[|]|<", "leq_")
# logging.info(f"Dropped {droppable_rows} rows for stratified K-fold with {single_support_classes} classes")
N_CLASSES = data["label"].nunique()  # 65

/gpfs/milgram/project/rtaylor/vs428/conda_envs/factcheck_env/lib/python3.7/site-packages/ipykernel_launcher.py:6: FutureWarning: The default value of regex will change from True to False in a future version.
  


In [21]:
data

PAT_ENC_CSN_ID  person_id  visit_occurrence_id   age  \
0             90893636   13534447             12119260  51.0   
1             92193999   12894663             12743657  50.0   
2             92197518   10675342             12831522  20.0   
3             92713043   11895224             13412537  41.0   
4             92771521   12740892             13973956  24.0   
...                ...        ...                  ...   ...   
178136       250327530   19420312            240922621  32.0   
178137       250327710   13558190            240922269  20.0   
178138       250328570   13573754            240923372  66.0   
178139       250329144   28466713            240922331  26.0   
178140       250329390   35446862            240922193  18.0   

        EdDisposition_AMA  EdDisposition_Admit  EdDisposition_Discharge  \
0                     NaN                  1.0                      NaN   
1                     NaN                  1.0                      NaN   
2                     NaN                  NaN                      1.0   
3                     NaN                  1.0                      NaN   
4                     NaN                  NaN                      1.0   
...                   ...                  ...                      ...   
178136                NaN                  NaN                      1.0   
178137                NaN                  NaN                      1.0   
178138                NaN                  NaN                      1.0   
178139                NaN                  1.0                      1.0   
178140                NaN                  NaN                      1.0   

        EdDisposition_Eloped  EdDisposition_Expired  \
0                        NaN                    NaN   
1                        NaN                    NaN   
2                        NaN                    NaN   
3                        NaN                    NaN   
4                        NaN                    NaN   
...                      ...                    ...   
178136                   NaN                    NaN   
178137                   NaN                    NaN   
178138                   NaN                    NaN   
178139                   NaN                    NaN   
178140                   NaN                    NaN   

        EdDisposition_LWBS after Triage  ...  last_BP_Diastolic  ed_SpO2  \
0                                   NaN  ...               43.0     94.0   
1                                   NaN  ...               75.0     98.0   
2                                   NaN  ...                NaN     99.0   
3                                   NaN  ...                NaN    100.0   
4                                   NaN  ...               88.0    100.0   
...                                 ...  ...                ...      ...   
178136                              NaN  ...               63.0     98.0   
178137                              NaN  ...               76.0    100.0   
178138                              NaN  ...               84.0     97.0   
178139                              NaN  ...               87.0     97.0   
178140                              NaN  ...               60.0    100.0   

        ed_Temp  ed_Patient Acuity  ed_Pulse  ed_Pain Score  ed_Resp  \
0          99.1                2.0     110.0            NaN     20.0   
1          98.4                3.0     109.0            NaN     19.0   
2          97.9                3.0      85.0            6.0     18.0   
3          98.5                3.0      59.0            NaN     16.0   
4          98.6                3.0      96.0            NaN     20.0   
...         ...                ...       ...            ...      ...   
178136     97.9                3.0     105.0           10.0     18.0   
178137     96.7                3.0     108.0            9.0     18.0   
178138     98.0                3.0      77.0            7.0     18.0   
178139     98.4                3.0      85.0

# Explore subset of features to train

In [7]:
with pd.option_context("display.max_rows", None):
    display(data["label"].value_counts())

Abdominal Pain, general                               68321
Acute cystitis                                        13695
Urolithiasis                                          11556
Colitis                                                9204
Constipation                                           8679
Appendicitis                                           6536
Diverticulitis                                         6138
Gastritis                                              5112
Bowel obstruction                                      4523
Ovarian cyst                                           4386
Flank pain/renal colic                                 4165
Pancreatitis                                           3716
Renal Failure                                          3588
Viral infection/influenza                              3376
Cholangitis                                            2950
Hernia                                                 2848
Peritonitis                             

In [8]:
desc_df = data.describe(include="all")

In [61]:
with pd.option_context("display.max_rows", None, "display.max_columns", None):
    display(desc_df.sort_values("max", axis=1, ascending=False))

PAT_ENC_CSN_ID  visit_occurrence_id      person_id  past_20447-9_avg  \
count     181502.00000         181502.00000   181502.00000          10.00000   
unique             NaN                  NaN            NaN               NaN   
top                NaN                  NaN            NaN               NaN   
freq               NaN                  NaN            NaN               NaN   
mean   174522712.00009      119782869.64931 20023494.35416      243066.60000   
std     43573248.40285       68957759.12857 11191801.61149      541600.09830   
min     90893636.00000       12119260.00000     4844.00000          20.00000   
25%    139286328.00000       58721905.00000 12347101.50000       11352.50000   
50%    177822803.50000      110803502.00000 13889487.00000       36900.00000   
75%    209942129.50000      182866711.50000 31681214.75000      182700.00000   
max    250329390.00000      240924331.00000 43619439.00000     1760000.00000   

        last_Pain Score  past_71690-2_avg  past_45194-8_avg  ed_45194-8_avg  \
count      105129.00000         313.00000        3511.00000      2475.00000   
unique              NaN               NaN               NaN             NaN   
top                 NaN               NaN               NaN             NaN   
freq                NaN               NaN               NaN             NaN   
mean           13.27461       12736.93584       18164.84342     18130.24040   
std          3084.39442       37643.46001       32598.72211     34146.20155   
min            -3.00000           1.00000           1.00000         1.00000   
25%             0.00000         100.00000           1.00000         1.00000   
50%             3.00000         375.00000         993.50000       734.00000   
75%             6.00000        5444.00000       23684.25000     21535.00000   
max       1000000.00000      394100.00000      292700.00000    259000.00000   

        past_792-2_avg  past_33762-6_avg  ed_3040-3_avg  past_3040-3_avg  \
count        137.00000        6756.00000    36923.00000      29013.00000   
unique             NaN               NaN            NaN              NaN   
top                NaN               NaN            NaN              NaN   
freq               NaN               NaN            NaN              NaN   
mean        3245.60706        4113.98136      241.58914        181.65413   
std        18099.39288       11795.29756     1979.78527       1417.30843   
min            0.00000           5.00000        3.00000          3.00000   
25%            2.00000         126.20000       26.00000         26.00000   
50%           22.00000         544.90000       51.00000         46.50000   
75%          296.00000        2472.75000      122.00000        112.00000   
max       184500.00000      175000.00000    97759.00000      97759.00000   

        ed_33762-6_avg  past_21198-7_avg  past_1795-4_avg  ed_1795-4_avg  \
count       1361.00000           9.00000         68.00000        1.00000   
unique             NaN               NaN              NaN            NaN   
top                NaN               NaN              NaN            NaN   
freq               NaN               NaN              NaN            NaN   
mean        5642.79030        8728.66667       1435.79412    56800.00000   
std        12065.48219       24247.84022       7944.07977            NaN   
min            5.00000           2.00000          3.00000    56800.00000   
25%          247.00000           2.00000         13.50000    56800.00000   
50%         1122.00000           2.00000         30.00000    56800.00000   
75%         4867.00000        1342.00000         33.25000    56800.00000   
max        78786.00000       73302.00000      56800.00000    56800.00000   

        past_26454-9_avg  Analgesic Opioid Agonists  past_2529-6_avg  \
count          139.00000                24862.00000        135.00000   
unique               NaN                        NaN              NaN   
top                  NaN                        NaN     

In [63]:
with pd.option_context("display.max_rows", None, "display.max_columns", None):

    display(data[data["Analgesic Opioid Agonists"] == 24396])

PAT_ENC_CSN_ID  person_id  visit_occurrence_id      age  \
175150       244567645   38328511            233892533 54.00000   

        EdDisposition_AMA  EdDisposition_Admit  EdDisposition_Discharge  \
175150            1.00000              1.00000                  1.00000   

        EdDisposition_Eloped  EdDisposition_Expired  \
175150               1.00000                    NaN   

        EdDisposition_LWBS after Triage  EdDisposition_LWBS before Triage  \
175150                              NaN                               NaN   

        EdDisposition_Observation  EdDisposition_Send to L&D  \
175150                        NaN                        NaN   

        EdDisposition_Transfer to Another Facility  \
175150                                         NaN   

        DepartmentName_BH EMERGENCY DEPARTMENT  \
175150                                     NaN   

        DepartmentName_BH FAIRFIELD URGENT CARE  \
175150                                      NaN   

        DepartmentName_GH EMERGENCY DEPARTMENT  \
175150                                     NaN   

        DepartmentName_LMH EMERGENCY DEPARTMENT  \
175150                                  1.00000   

        DepartmentName_LMH EMERGENCY PEQUOT  \
175150                                  NaN   

        DepartmentName_MC EMERGENCY DEPARTMENT  DepartmentName_MC URGENT CARE  \
175150                                     NaN                            NaN   

        DepartmentName_SRC EMERGENCY DEPARTMENT  \
175150                                  1.00000   

        DepartmentName_WH EMERGENCY DEPARTMENT  \
175150                                     NaN   

        DepartmentName_YHC ACUTE AND INPATIENT CARE  \
175150                                          NaN   

        DepartmentName_YNH CRITICAL CARE TRANSPORT  \
175150                                         NaN   

        DepartmentName_YNH EMERGENCY ADULT  \
175150                                 NaN   

        DepartmentName_YNH EMERGENCY PEDIATRIC  \
175150                                     NaN   

        DepartmentName_YNH EMERGENCY SHORELINE  \
175150                                     NaN   

        DepartmentName_YNH PERIOP SVCS SP  Sex_Female  Sex_Male  Sex_Unknown  \
175150                                NaN         NaN   1.00000          NaN   

        GenderIdentity_Choose not to disclose  GenderIdentity_Female  \
175150                                    NaN                    NaN   

        GenderIdentity_Gender non-conforming  GenderIdentity_Genderqueer  \
175150                                   NaN                         NaN   

        GenderIdentity_Intersex  GenderIdentity_Male  GenderIdentity_Other  \
175150                      NaN              1.00000                   NaN   

        GenderIdentity_Transgender Female / Male-to-Female  \
175150                                                NaN    

        GenderIdentity_Transgender Male / Female-to-Male  FirstRace_Asian  \
175150                                               NaN              NaN   

        FirstRace_Black or African American  FirstRace_Native Hawaiian  \
175150                                  NaN                        NaN   

        FirstRace_Native Hawaiian or Other Pacific Islander  FirstRace_Other  \
175150                                                NaN                NaN   

        FirstRace_Other Pacific Islander  FirstRace_Other/Not Listed  \
175150                               NaN                         NaN   

        FirstRace_Patient Refused  FirstRace_Unknown  \
175150                        NaN                NaN   

        FirstRace_White or Caucasian  Ethnicity_Hispanic or Latino  \
175150                       1.00000                           NaN   

        Ethnicity_Non-Hispanic  Ethnicity_Patient Refused  Ethnicity_Unknown  \
175150                 1.00000                        NaN                NaN   

        PreferredLanguage_Albanian  PreferredLanguage_Arabic  \
175

In [11]:
with pd.option_context("display.max_rows", None, "display.max_columns", None):
    display(data.columns[((data.shape[0] - data.isnull().sum()) == 0)])

Index(['DepartmentName_YNH PERIOP SVCS SP', 'FAC018', 'INJ015', 'MUS005',
       'MUS018', 'NEO054', 'Antileprotic - Immunomodulators',
       'Platelet Aggregation Inhibitors - Quinazoline Agents',
       'Antileprotic - Phenazine Dye Derivatives',
       'Nutritional Product - MSUD Specific Formulation',
       ...
       'past_3187-2_avg', 'past_17842-6_avg', 'past_47657-2_avg',
       'past_28059-4_avg', 'past_1_avg', 'past_3537-8_avg', 'past_69797-9_avg',
       'past_8087-9_avg', 'past_3457-9_avg', 'past_11034-6_avg'],
      dtype='object', length=866)

In [69]:
meds = pd.read_csv("/home/vs428/project/Data/abd_pain_cohort/abd_outpt_med.csv")
demos = pd.read_csv("/home/vs428/project/Data/abd_pain_cohort/abd_demos.csv")
diags = pd.read_csv("/home/vs428/project/Data/abd_pain_cohort/abd_ed_diagnoses.csv")

In [13]:
data[
    data.columns.intersection(
        data.columns[(((data.shape[0] - data.isnull().sum())) > 10)]
    )
]
# data

PAT_ENC_CSN_ID  person_id  visit_occurrence_id   age  \
0             90893636   13534447             12119260  51.0   
1             92193999   12894663             12743657  50.0   
2             92197518   10675342             12831522  20.0   
3             92713043   11895224             13412537  41.0   
4             92771521   12740892             13973956  24.0   
...                ...        ...                  ...   ...   
181497       250327530   19420312            240922621  32.0   
181498       250327710   13558190            240922269  20.0   
181499       250328570   13573754            240923372  66.0   
181500       250329144   28466713            240922331  26.0   
181501       250329390   35446862            240922193  18.0   

        EdDisposition_AMA  EdDisposition_Admit  EdDisposition_Discharge  \
0                     NaN                  1.0                      NaN   
1                     NaN                  1.0                      NaN   
2                     NaN                  NaN                      1.0   
3                     NaN                  1.0                      NaN   
4                     NaN                  NaN                      1.0   
...                   ...                  ...                      ...   
181497                NaN                  NaN                      1.0   
181498                NaN                  NaN                      1.0   
181499                NaN                  NaN                      1.0   
181500                NaN                  1.0                      1.0   
181501                NaN                  NaN                      1.0   

        EdDisposition_Eloped  EdDisposition_Expired  \
0                        NaN                    NaN   
1                        NaN                    NaN   
2                        NaN                    NaN   
3                        NaN                    NaN   
4                        NaN                    NaN   
...                      ...                    ...   
181497                   NaN                    NaN   
181498                   NaN                    NaN   
181499                   NaN                    NaN   
181500                   NaN                    NaN   
181501                   NaN                    NaN   

        EdDisposition_LWBS after Triage  ...  last_BP_Diastolic  ed_SpO2  \
0                                   NaN  ...               43.0     94.0   
1                                   NaN  ...               75.0     98.0   
2                                   NaN  ...                NaN     99.0   
3                                   NaN  ...                NaN    100.0   
4                                   NaN  ...               88.0    100.0   
...                                 ...  ...                ...      ...   
181497                              NaN  ...               63.0     98.0   
181498                              NaN  ...               76.0    100.0   
181499                              NaN  ...               84.0     97.0   
181500                              NaN  ...               87.0     97.0   
181501                              NaN  ...               60.0    100.0   

        ed_Temp  ed_Patient Acuity  ed_Pulse  ed_Pain Score  ed_Resp  \
0          99.1                2.0     110.0            NaN     20.0   
1          98.4                3.0     109.0            NaN     19.0   
2          97.9                3.0      85.0            6.0     18.0   
3          98.5                3.0      59.0            NaN     16.0   
4          98.6                3.0      96.0            NaN     20.0   
...         ...                ...       ...            ...      ...   
181497     97.9                3.0     105.0           10.0     18.0   
181498     96.7                3.0     108.0            9.0     18.0   
181499     98.0                3.0      77.0            7.0     18.0   
181500     98.4                3.0      85.0

In [14]:
data.columns[((data.shape[0] - data.isnull().sum()) == 0)]
4097 - 866

3231

In [104]:
data["C1 Esterase Inhibitor Agents"].value_counts(dropna=False)

NaN        181497
7.00000         2
1.00000         1
2.00000         1
8.00000         1
Name: C1 Esterase Inhibitor Agents, dtype: int64

In [92]:
data_subset = data[
    data.columns.intersection(
        data.columns[(((data.shape[0] - data.isnull().sum())) > 100)]
    )
]
from sklearn.preprocessing import StandardScaler

scaler = MinMaxScaler()

In [93]:
with pd.option_context("display.max_columns", None):
    display(data_subset)

PAT_ENC_CSN_ID  person_id  visit_occurrence_id      age  \
0             90893636   13534447             12119260 51.00000   
1             92193999   12894663             12743657 50.00000   
2             92197518   10675342             12831522 20.00000   
3             92713043   11895224             13412537 41.00000   
4             92771521   12740892             13973956 24.00000   
...                ...        ...                  ...      ...   
181497       250327530   19420312            240922621 32.00000   
181498       250327710   13558190            240922269 20.00000   
181499       250328570   13573754            240923372 66.00000   
181500       250329144   28466713            240922331 26.00000   
181501       250329390   35446862            240922193 18.00000   

        EdDisposition_AMA  EdDisposition_Admit  EdDisposition_Discharge  \
0                     NaN              1.00000                      NaN   
1                     NaN              1.00000                      NaN   
2                     NaN                  NaN                  1.00000   
3                     NaN              1.00000                      NaN   
4                     NaN                  NaN                  1.00000   
...                   ...                  ...                      ...   
181497                NaN                  NaN                  1.00000   
181498                NaN                  NaN                  1.00000   
181499                NaN                  NaN                  1.00000   
181500                NaN              1.00000                  1.00000   
181501                NaN                  NaN                  1.00000   

        EdDisposition_Eloped  EdDisposition_LWBS after Triage  \
0                        NaN                              NaN   
1                        NaN                              NaN   
2                        NaN                              NaN   
3                        NaN                              NaN   
4                        NaN                              NaN   
...                      ...                              ...   
181497                   NaN                              NaN   
181498                   NaN                              NaN   
181499                   NaN                              NaN   
181500                   NaN                              NaN   
181501                   NaN                              NaN   

        EdDisposition_Observation  EdDisposition_Transfer to Another Facility  \
0                             NaN                                         NaN   
1                             NaN                                         NaN   
2                             NaN                                         NaN   
3                             NaN                                         NaN   
4                             NaN                                         NaN   
...                           ...                                         ...   
181497                        NaN                                         NaN   
181498                        NaN                                         NaN   
181499                        NaN                                         NaN   
181500                        NaN                                         NaN   
181501                        NaN                                         NaN   

        DepartmentName_BH EMERGENCY DEPARTMENT  \
0                                          NaN   
1                                          NaN   
2                                          NaN   
3                                          NaN   
4                                          NaN   
...                                        ...   
181497                                     NaN   
181498                                     NaN   
181499                                     NaN   
181500                                     NaN  

In [96]:
out = scaler.fit_transform(
    data_subset[
        [
            "DepartmentName_GH EMERGENCY DEPARTMENT",
            "past_50562-8_avg",
            "last_Temp",
            "last_BP_Systolic",
            "last_BP_Diastolic",
            "ed_Pulse",
            "ed_Pain Score",
        ]
    ]
)

In [110]:
data[
    [
        "ed_10331-7_neg",
        "ed_882-1_o positive",
        "ed_882-1_b positive",
        "ed_882-1_a positive",
        "ed_14578-9_b pos",
        "ed_14578-9_o pos",
        "ed_50957-0_performed",
        "ed_14578-9_a pos",
        "ed_890-4_pos",
        "ed_890-4_neg",
        "ed_10331-7_pos",
        "ed_19642-8",
        "ed_1744-2",
        "ed_14310-7",
        "ed_13955-0",
        "ed_11580-8",
        "ed_57751-0",
    ]
].describe()

ed_10331-7_neg  ed_882-1_o positive  ed_882-1_b positive  \
count       552.00000            499.00000            122.00000   
mean          1.00000              1.01804              1.00820   
std           0.00000              0.13322              0.09054   
min           1.00000              1.00000              1.00000   
25%           1.00000              1.00000              1.00000   
50%           1.00000              1.00000              1.00000   
75%           1.00000              1.00000              1.00000   
max           1.00000              2.00000              2.00000   

       ed_882-1_a positive  ed_14578-9_b pos  ed_14578-9_o pos  \
count            332.00000         199.00000         704.00000   
mean               1.03614           1.00000           1.00000   
std                0.18693           0.00000           0.00000   
min                1.00000           1.00000           1.00000   
25%                1.00000           1.00000           1.00000   
50%                1.00000           1.00000           1.00000   
75%                1.00000           1.00000           1.00000   
max                2.00000           1.00000           1.00000   

       ed_50957-0_performed  ed_14578-9_a pos  ed_890-4_pos  ed_890-4_neg  \
count            3098.00000         435.00000     131.00000    5478.00000   
mean                1.00065           1.00000       1.25954       1.00000   
std                 0.02540           0.00000       0.58950       0.00000   
min                 1.00000           1.00000       1.00000       1.00000   
25%                 1.00000           1.00000       1.00000       1.00000   
50%                 1.00000           1.00000       1.00000       1.00000   
75%                 1.00000           1.00000       1.00000       1.00000   
max                 2.00000           1.00000       5.00000       1.00000   

       ed_10331-7_pos  ed_19642-8   ed_1744-2  ed_14310-7  ed_13955-0  \
count      4804.00000   193.00000 61017.00000   179.00000   110.00000   
mean          1.00000     1.00000     1.00249     1.00000     1.00000   
std           0.00000     0.00000     0.04985     0.00000     0.00000   
min           1.00000     1.00000     1.00000     1.00000     1.00000   
25%           1.00000     1.00000     1.00000     1.00000     1.00000   
50%           1.00000     1.00000     1.00000     1.00000     1.00000   
75%           1.00000     1.00000     1.00000     1.00000     1.00000   
max           1.00000     1.00000     2.00000     1.00000     1.00000   

       ed_11580-8  ed_57751-0  
count  1274.00000 24040.00000  
mean      1.12951     1.00067  
std       0.33590     0.02579  
min       1.00000     1.00000  
25%       1.00000     1.00000  
50%       1.00000     1.00000  
75%       1.00000     1.00000  
max       2.00000     2.00000

In [111]:
# data_subset.shape, data.shape
print(list(data.columns))

['PAT_ENC_CSN_ID', 'person_id', 'visit_occurrence_id', 'age', 'EdDisposition_AMA', 'EdDisposition_Admit', 'EdDisposition_Discharge', 'EdDisposition_Eloped', 'EdDisposition_Expired', 'EdDisposition_LWBS after Triage', 'EdDisposition_LWBS before Triage', 'EdDisposition_Observation', 'EdDisposition_Send to L&D', 'EdDisposition_Transfer to Another Facility', 'DepartmentName_BH EMERGENCY DEPARTMENT', 'DepartmentName_BH FAIRFIELD URGENT CARE', 'DepartmentName_GH EMERGENCY DEPARTMENT', 'DepartmentName_LMH EMERGENCY DEPARTMENT', 'DepartmentName_LMH EMERGENCY PEQUOT', 'DepartmentName_MC EMERGENCY DEPARTMENT', 'DepartmentName_MC URGENT CARE', 'DepartmentName_SRC EMERGENCY DEPARTMENT', 'DepartmentName_WH EMERGENCY DEPARTMENT', 'DepartmentName_YHC ACUTE AND INPATIENT CARE', 'DepartmentName_YNH CRITICAL CARE TRANSPORT', 'DepartmentName_YNH EMERGENCY ADULT', 'DepartmentName_YNH EMERGENCY PEDIATRIC', 'DepartmentName_YNH EMERGENCY SHORELINE', 'DepartmentName_YNH PERIOP SVCS SP', 'Sex_Female', 'Sex_Mal

In [ ]:
std_scaler = StandardScaler()
minmax_scaler = MinMaxScaler()

avg_cols = data.columns[data.columns.str.contains("_avg")].union(pd.Index(["age"]))
vital_cols = pd.Index(
    [
        "last_SpO2",
        "last_Temp",
        "last_Patient Acuity",
        "last_Pulse",
        "last_Pain Score",
        "last_Resp",
        "last_BP_Systolic",
        "last_BP_Diastolic",
        "ed_SpO2",
        "ed_Temp",
        "ed_Patient Acuity",
        "ed_Pulse",
        "ed_Pain Score",
        "ed_Resp",
        "ed_BP_Systolic",
        "ed_BP_Diastolic",
    ]
)

In [130]:
all_other_cols = data.columns.difference(avg_cols, sort=False)
all_other_cols = all_other_cols.difference(vital_cols, sort=False)
all_other_cols = all_other_cols.difference(pd.Index(["label"]), sort=False)

In [126]:
# cols with Normal-ish distros
normal_cols = avg_cols.union(vital_cols)
# non-Normal distros

In [132]:
std_scaler.fit(data[normal_cols])

/gpfs/milgram/project/rtaylor/vs428/conda_envs/factcheck_env/lib/python3.7/site-packages/sklearn/utils/extmath.py:985: RuntimeWarning: invalid value encountered in true_divide
  updated_mean = (last_sum + new_sum) / updated_sample_count
/gpfs/milgram/project/rtaylor/vs428/conda_envs/factcheck_env/lib/python3.7/site-packages/sklearn/utils/extmath.py:990: RuntimeWarning: invalid value encountered in true_divide
  T = new_sum / new_sample_count
/gpfs/milgram/project/rtaylor/vs428/conda_envs/factcheck_env/lib/python3.7/site-packages/sklearn/utils/extmath.py:1020: RuntimeWarning: invalid value encountered in true_divide
  new_unnormalized_variance -= correction ** 2 / new_sample_count


StandardScaler()

In [ ]:
std_scaler.fit(data[normal_cols])
minmax_scaler.fit(data[all_other_cols])

# Select very simple base class

In [10]:
with pd.option_context("display.max_rows", None, "display.max_columns", None):

    print(list((data.columns)))

['PAT_ENC_CSN_ID', 'person_id', 'visit_occurrence_id', 'age', 'EdDisposition_AMA', 'EdDisposition_Admit', 'EdDisposition_Discharge', 'EdDisposition_Eloped', 'EdDisposition_Expired', 'EdDisposition_LWBS after Triage', 'EdDisposition_LWBS before Triage', 'EdDisposition_Observation', 'EdDisposition_Send to L&D', 'EdDisposition_Transfer to Another Facility', 'DepartmentName_BH EMERGENCY DEPARTMENT', 'DepartmentName_BH FAIRFIELD URGENT CARE', 'DepartmentName_GH EMERGENCY DEPARTMENT', 'DepartmentName_LMH EMERGENCY DEPARTMENT', 'DepartmentName_LMH EMERGENCY PEQUOT', 'DepartmentName_MC EMERGENCY DEPARTMENT', 'DepartmentName_MC URGENT CARE', 'DepartmentName_SRC EMERGENCY DEPARTMENT', 'DepartmentName_WH EMERGENCY DEPARTMENT', 'DepartmentName_YHC ACUTE AND INPATIENT CARE', 'DepartmentName_YNH CRITICAL CARE TRANSPORT', 'DepartmentName_YNH EMERGENCY ADULT', 'DepartmentName_YNH EMERGENCY PEDIATRIC', 'DepartmentName_YNH EMERGENCY SHORELINE', 'DepartmentName_YNH PERIOP SVCS SP', 'Sex_Female', 'Sex_Mal

In [104]:
x = torch.zeros(5, 5)
y = torch.rand(5, 5)

In [121]:
x[:, []] = np.array([])

TypeError: can't assign a numpy.ndarray to a torch.FloatTensor

array([], dtype=float64)

# Create WikEM Multilabel dataset

In [12]:
single_support_classes = set(
    data["label"].value_counts()[data["label"].value_counts() <= 1].index
)
# droppable_rows = data['label'].isin(single_support_classes).sum()
data = data[~data["label"].isin(single_support_classes)]

In [13]:
grouped = data.groupby("PAT_ENC_CSN_ID")

In [14]:
labels = [group["label"].tolist() for grp_id, group in grouped]

In [15]:
grouped_unq_pts = grouped.first().reset_index()

In [16]:
grouped_unq_pts["multilabel"] = pd.Series(labels)

In [17]:
grouped_unq_pts = grouped_unq_pts.drop("label", axis=1)
grouped_unq_pts

PAT_ENC_CSN_ID  person_id  visit_occurrence_id   age  \
0             90893636   13534447             12119260  51.0   
1             92193999   12894663             12743657  50.0   
2             92197518   10675342             12831522  20.0   
3             92713043   11895224             13412537  41.0   
4             92771521   12740892             13973956  24.0   
...                ...        ...                  ...   ...   
162300       250327530   19420312            240922621  32.0   
162301       250327710   13558190            240922269  20.0   
162302       250328570   13573754            240923372  66.0   
162303       250329144   28466713            240922331  26.0   
162304       250329390   35446862            240922193  18.0   

        EdDisposition_AMA  EdDisposition_Admit  EdDisposition_Discharge  \
0                     NaN                  1.0                      NaN   
1                     NaN                  1.0                      NaN   
2                     NaN                  NaN                      1.0   
3                     NaN                  1.0                      NaN   
4                     NaN                  NaN                      1.0   
...                   ...                  ...                      ...   
162300                NaN                  NaN                      1.0   
162301                NaN                  NaN                      1.0   
162302                NaN                  NaN                      1.0   
162303                NaN                  1.0                      1.0   
162304                NaN                  NaN                      1.0   

        EdDisposition_Eloped  EdDisposition_Expired  \
0                        NaN                    NaN   
1                        NaN                    NaN   
2                        NaN                    NaN   
3                        NaN                    NaN   
4                        NaN                    NaN   
...                      ...                    ...   
162300                   NaN                    NaN   
162301                   NaN                    NaN   
162302                   NaN                    NaN   
162303                   NaN                    NaN   
162304                   NaN                    NaN   

        EdDisposition_LWBS after Triage  ...  last_BP_Diastolic  ed_SpO2  \
0                                   NaN  ...               43.0     94.0   
1                                   NaN  ...               75.0     98.0   
2                                   NaN  ...                NaN     99.0   
3                                   NaN  ...                NaN    100.0   
4                                   NaN  ...               88.0    100.0   
...                                 ...  ...                ...      ...   
162300                              NaN  ...               63.0     98.0   
162301                              NaN  ...               76.0    100.0   
162302                              NaN  ...               84.0     97.0   
162303                              NaN  ...               87.0     97.0   
162304                              NaN  ...               60.0    100.0   

        ed_Temp  ed_Patient Acuity  ed_Pulse  ed_Pain Score  ed_Resp  \
0          99.1                2.0     110.0            NaN     20.0   
1          98.4                3.0     109.0            NaN     19.0   
2          97.9                3.0      85.0            6.0     18.0   
3          98.5                3.0      59.0            NaN     16.0   
4          98.6                3.0      96.0            NaN     20.0   
...         ...                ...       ...            ...      ...   
162300     97.9                3.0     105.0           10.0     18.0   
162301     96.7                3.0     108.0            9.0     18.0   
162302     98.0                3.0      77.0            7.0     18.0   
162303     98.4                3.0      85.0

In [30]:
le = sklearn.preprocessing.LabelEncoder()

In [32]:
le.fit(data["label"])

LabelEncoder()

In [23]:
grouped_unq_pts.to_pickle(
    f"/gpfs/milgram/project/rtaylor/shared/ABDPain_EarlyDiags/unq_pt_enc_single_label_clean_label_nomismatches.csv",
)

# Condense dataset down from one hot encoding for embedding vector

In [10]:
data = pd.read_pickle(
    f"/gpfs/milgram/project/rtaylor/shared/ABDPain_EarlyDiags/unq_pt_enc_clean_multilabel_nomismatches.pkl"
)

In [11]:
data

PAT_ENC_CSN_ID  person_id  visit_occurrence_id   age  \
0             90893636   13534447             12119260  51.0   
1             92193999   12894663             12743657  50.0   
2             92197518   10675342             12831522  20.0   
3             92713043   11895224             13412537  41.0   
4             92771521   12740892             13973956  24.0   
...                ...        ...                  ...   ...   
162300       250327530   19420312            240922621  32.0   
162301       250327710   13558190            240922269  20.0   
162302       250328570   13573754            240923372  66.0   
162303       250329144   28466713            240922331  26.0   
162304       250329390   35446862            240922193  18.0   

        EdDisposition_AMA  EdDisposition_Admit  EdDisposition_Discharge  \
0                     NaN                  1.0                      NaN   
1                     NaN                  1.0                      NaN   
2                     NaN                  NaN                      1.0   
3                     NaN                  1.0                      NaN   
4                     NaN                  NaN                      1.0   
...                   ...                  ...                      ...   
162300                NaN                  NaN                      1.0   
162301                NaN                  NaN                      1.0   
162302                NaN                  NaN                      1.0   
162303                NaN                  1.0                      1.0   
162304                NaN                  NaN                      1.0   

        EdDisposition_Eloped  EdDisposition_Expired  \
0                        NaN                    NaN   
1                        NaN                    NaN   
2                        NaN                    NaN   
3                        NaN                    NaN   
4                        NaN                    NaN   
...                      ...                    ...   
162300                   NaN                    NaN   
162301                   NaN                    NaN   
162302                   NaN                    NaN   
162303                   NaN                    NaN   
162304                   NaN                    NaN   

        EdDisposition_LWBS after Triage  ...  last_BP_Diastolic  ed_SpO2  \
0                                   NaN  ...               43.0     94.0   
1                                   NaN  ...               75.0     98.0   
2                                   NaN  ...                NaN     99.0   
3                                   NaN  ...                NaN    100.0   
4                                   NaN  ...               88.0    100.0   
...                                 ...  ...                ...      ...   
162300                              NaN  ...               63.0     98.0   
162301                              NaN  ...               76.0    100.0   
162302                              NaN  ...               84.0     97.0   
162303                              NaN  ...               87.0     97.0   
162304                              NaN  ...               60.0    100.0   

        ed_Temp  ed_Patient Acuity  ed_Pulse  ed_Pain Score  ed_Resp  \
0          99.1                2.0     110.0            NaN     20.0   
1          98.4                3.0     109.0            NaN     19.0   
2          97.9                3.0      85.0            6.0     18.0   
3          98.5                3.0      59.0            NaN     16.0   
4          98.6                3.0      96.0            NaN     20.0   
...         ...                ...       ...            ...      ...   
162300     97.9                3.0     105.0           10.0     18.0   
162301     96.7                3.0     108.0            9.0     18.0   
162302     98.0                3.0      77.0            7.0     18.0   
162303     98.4                3.0      85.0

In [12]:
def undummify(df, prefix_sep="_"):
    cols2collapse = {
        item.split(prefix_sep)[0]: (prefix_sep in item) for item in df.columns
    }
    series_list = []
    for col, needs_to_collapse in cols2collapse.items():
        if needs_to_collapse:
            undummified = (
                df.filter(like=col)
                .idxmax(axis=1)
                .apply(lambda x: x.split(prefix_sep, maxsplit=1)[1])
                .rename(col)
            )
            series_list.append(undummified)
        else:
            series_list.append(df[col])
    undummified_df = pd.concat(series_list, axis=1)
    return undummified_df

In [14]:
print(list(data.columns))

['PAT_ENC_CSN_ID', 'person_id', 'visit_occurrence_id', 'age', 'EdDisposition_AMA', 'EdDisposition_Admit', 'EdDisposition_Discharge', 'EdDisposition_Eloped', 'EdDisposition_Expired', 'EdDisposition_LWBS after Triage', 'EdDisposition_LWBS before Triage', 'EdDisposition_Observation', 'EdDisposition_Send to L&D', 'EdDisposition_Transfer to Another Facility', 'DepartmentName_BH EMERGENCY DEPARTMENT', 'DepartmentName_BH FAIRFIELD URGENT CARE', 'DepartmentName_GH EMERGENCY DEPARTMENT', 'DepartmentName_LMH EMERGENCY DEPARTMENT', 'DepartmentName_LMH EMERGENCY PEQUOT', 'DepartmentName_MC EMERGENCY DEPARTMENT', 'DepartmentName_MC URGENT CARE', 'DepartmentName_SRC EMERGENCY DEPARTMENT', 'DepartmentName_WH EMERGENCY DEPARTMENT', 'DepartmentName_YHC ACUTE AND INPATIENT CARE', 'DepartmentName_YNH CRITICAL CARE TRANSPORT', 'DepartmentName_YNH EMERGENCY ADULT', 'DepartmentName_YNH EMERGENCY PEDIATRIC', 'DepartmentName_YNH EMERGENCY SHORELINE', 'DepartmentName_YNH PERIOP SVCS SP', 'Sex_Female', 'Sex_Mal